<a href="https://colab.research.google.com/github/JoshFowlkes/DS-Unit-2-Regression-Classification/blob/master/module3/assignment_regression_classification_3.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Lambda School Data Science, Unit 2: Predictive Modeling

# Regression & Classification, Module 3

## Assignment

We're going back to our other **New York City** real estate dataset. Instead of predicting apartment rents, you'll predict property sales prices.

But not just for condos in Tribeca...

Instead, predict property sales prices for **One Family Dwellings** (`BUILDING_CLASS_CATEGORY` == `'01 ONE FAMILY DWELLINGS'`) using a subset of the data where the **sale price was more than \\$100 thousand and less than $2 million.** 

The [NYC Department of Finance](https://www1.nyc.gov/site/finance/taxes/property-rolling-sales-data.page) has a glossary of property sales terms and NYC Building Class Code Descriptions. The data comes from the [NYC OpenData](https://data.cityofnewyork.us/browse?q=NYC%20calendar%20sales) portal.


- [ ] Do train/test split. Use data from January — March 2019 to train. Use data from April 2019 to test.
- [ ] Do exploratory visualizations with Seaborn.
- [ ] Do one-hot encoding of categorical features.
- [ ] Do feature selection with `SelectKBest`.
- [ ] Fit a linear regression model with multiple features.
- [ ] Get mean absolute error for the test set.
- [ ] As always, commit your notebook to your fork of the GitHub repo.


## Stretch Goals
- [ ] Add your own stretch goal(s) !
- [ ] Do [feature scaling](https://scikit-learn.org/stable/modules/preprocessing.html).
- [ ] Learn more about feature selection:
    - ["Permutation importance"](https://www.kaggle.com/dansbecker/permutation-importance)
    - [scikit-learn's User Guide for Feature Selection](https://scikit-learn.org/stable/modules/feature_selection.html)
    - [mlxtend](http://rasbt.github.io/mlxtend/) library
    - scikit-learn-contrib libraries: [boruta_py](https://github.com/scikit-learn-contrib/boruta_py) & [stability-selection](https://github.com/scikit-learn-contrib/stability-selection)
    - [_Feature Engineering and Selection_](http://www.feat.engineering/) by Kuhn & Johnson.
- [ ] Try [statsmodels](https://www.statsmodels.org/stable/index.html) if you’re interested in more inferential statistical approach to linear regression and feature selection, looking at p values and 95% confidence intervals for the coefficients.
- [ ] Read [_An Introduction to Statistical Learning_](http://faculty.marshall.usc.edu/gareth-james/ISL/ISLR%20Seventh%20Printing.pdf), Chapters 1-3, for more math & theory, but in an accessible, readable way (without an excessive amount of formulas or academic pre-requisites).
(That book is good regardless of whether your cultural worldview is inferential statistics or predictive machine learning)
- [ ] Read Leo Breiman's paper, ["Statistical Modeling: The Two Cultures"](https://projecteuclid.org/download/pdf_1/euclid.ss/1009213726)
- [ ] Try [scikit-learn pipelines](https://scikit-learn.org/stable/modules/compose.html):

> Pipeline can be used to chain multiple estimators into one. This is useful as there is often a fixed sequence of steps in processing the data, for example feature selection, normalization and classification. Pipeline serves multiple purposes here:

> - **Convenience and encapsulation.** You only have to call fit and predict once on your data to fit a whole sequence of estimators.
> - **Joint parameter selection.** You can grid search over parameters of all estimators in the pipeline at once.
> - **Safety.** Pipelines help avoid leaking statistics from your test data into the trained model in cross-validation, by ensuring that the same samples are used to train the transformers and predictors.

In [1]:
# If you're in Colab...
import os, sys
in_colab = 'google.colab' in sys.modules

if in_colab:
    # Install required python packages:
    # category_encoders, version >= 2.0
    # pandas-profiling, version >= 2.0
    # plotly, version >= 4.0
    !pip install --upgrade category_encoders pandas-profiling plotly
    
    # Pull files from Github repo
    os.chdir('/content')
    !git init .
    !git remote add origin https://github.com/LambdaSchool/DS-Unit-2-Regression-Classification.git
    !git pull origin master
    
    # Change into directory for module
    os.chdir('module3')

     |████████████████████████████████| 92kB 5.7MB/s 
     |████████████████████████████████| 133kB 15.6MB/s 
     |████████████████████████████████| 7.1MB 13.0MB/s 
     |████████████████████████████████| 614kB 33.6MB/s 
     |████████████████████████████████| 225kB 43.2MB/s 
     |████████████████████████████████| 768kB 40.3MB/s 
     |████████████████████████████████| 51kB 19.5MB/s 
     |████████████████████████████████| 194kB 30.5MB/s 
     |████████████████████████████████| 737kB 43.9MB/s 
     |████████████████████████████████| 51kB 18.6MB/s 
  Created wheel for pandas-profiling: filename=pandas_profiling-2.3.0-py2.py3-none-any.whl size=145036 sha256=230679d794a069aaffabf1a95ed2e4c45180c2e1d4239c022641bf7275835485
  Stored in directory: /root/.cache/pip/wheels/ce/c7/f1/dbfef4848ebb048cb1d4a22d1ed0c62d8ff2523747235e19fe
  Created wheel for htmlmin: filename=htmlmin-0.1.12-cp36-none-any.whl size=27085 sha256=93f9cbdf8bd9808376679489150130bca8f7620f210a7b99cbc08aafcfb53f30
  Stored

In [0]:
# Ignore this Numpy warning when using Plotly Express:
# FutureWarning: Method .ptp is deprecated and will be removed in a future version. Use numpy.ptp instead.
import warnings
warnings.filterwarnings(action='ignore', category=FutureWarning, module='numpy')

In [0]:
import pandas as pd
import pandas_profiling
import numpy as np

# Read New York City property sales data
df = pd.read_csv('../data/NYC_Citywide_Rolling_Calendar_Sales.csv')

# Change column names: replace spaces with underscores
df.columns = [col.replace(' ', '_') for col in df]

# SALE_PRICE was read as strings.
# Remove symbols, convert to integer
df['SALE_PRICE'] = (
    df['SALE_PRICE']
    .str.replace('$','')
    .str.replace('-','')
    .str.replace(',','')
    .astype(int)
)



In [26]:
import matplotlib.pyplot as plt 
import pandas_profiling
df.profile_report()

In [27]:
pd.options.display.float_format = '{:,.0f}'.format # this adds comma sep, and changes big floats to rounded #
df.describe()

BOROUGH  BLOCK    LOT  ...  YEAR_BUILT  TAX_CLASS_AT_TIME_OF_SALE  SALE_PRICE
count   23,040 23,040 23,040  ...      23,005                     23,040      23,040
mean         3  4,459    354  ...       1,820                          2   1,328,133
std          1  3,713    628  ...         488                          1  10,253,944
min          1      1      1  ...           0                          1           0
25%          2  1,341     22  ...       1,920                          1           0
50%          3  3,546     49  ...       1,940                          1     455,000
75%          4  6,674    375  ...       1,965                          2     875,000
max          5 16,350  9,057  ...       2,019                          4 850,000,000

[8 rows x 12 columns]

In [28]:
df.head()

BOROUGH             NEIGHBORHOOD  ... SALE_PRICE   SALE_DATE
0        1                  CHELSEA  ...          0  01/01/2019
1        1                  FASHION  ...          0  01/01/2019
2        1                  FASHION  ...          0  01/01/2019
3        1   GREENWICH VILLAGE-WEST  ...          0  01/01/2019
4        1  UPPER EAST SIDE (59-79)  ...          0  01/01/2019

[5 rows x 21 columns]

# Train/Test Split

In [29]:
df['SALE_DATE'] = pd.to_datetime(df['SALE_DATE'], infer_datetime_format=True)
df['SALE_DATE'].describe()

count                   23040
unique                    120
top       2019-01-24 00:00:00
freq                      480
first     2019-01-01 00:00:00
last      2019-04-30 00:00:00
Name: SALE_DATE, dtype: object

In [30]:
cutoff = pd.to_datetime('2019-04-01')
train = df[df.SALE_DATE < cutoff]
test = df[df.SALE_DATE >= cutoff]
train.shape, test.shape

((18167, 21), (4873, 21))

# Explanatory Visuals Using Seaborn

In [9]:
import plotly.express as px
px.scatter(train, x='YEAR_BUILT', y='SALE_PRICE', color='SALE_PRICE')

# One-HOT Encoding of Categorical Features

In [10]:
train.describe(exclude='number').T.sort_values(by='unique')

count  ...                 last
TAX_CLASS_AT_PRESENT            18167  ...                  NaN
BUILDING_CLASS_CATEGORY         18167  ...                  NaN
SALE_DATE                       18167  ...  2019-03-31 00:00:00
BUILDING_CLASS_AT_PRESENT       18167  ...                  NaN
BUILDING_CLASS_AT_TIME_OF_SALE  18167  ...                  NaN
NEIGHBORHOOD                    18167  ...                  NaN
APARTMENT_NUMBER                 3972  ...                  NaN
LAND_SQUARE_FEET                18139  ...                  NaN
ADDRESS                         18167  ...                  NaN

[9 rows x 6 columns]

In [11]:
train['TAX_CLASS_AT_PRESENT'].value_counts()

1     8911
2     6255
4     1258
2A     588
2C     464
1A     289
1B     209
2B     128
1D      34
1C      31
Name: TAX_CLASS_AT_PRESENT, dtype: int64

In [12]:
train.groupby('TAX_CLASS_AT_PRESENT')['SALE_PRICE'].mean()

TAX_CLASS_AT_PRESENT
1     4.905709e+05
1A    3.615866e+05
1B    7.556957e+05
1C    1.051295e+06
1D    3.582324e+05
2     1.345565e+06
2A    8.459622e+05
2B    1.785369e+06
2C    1.102988e+06
4     6.186266e+06
Name: SALE_PRICE, dtype: float64

In [13]:
import category_encoders as ce
encoder = ce.OneHotEncoder(use_cat_names=True)
encoded = encoder.fit_transform(train['TAX_CLASS_AT_PRESENT'])
encoded.head()

TAX_CLASS_AT_PRESENT_2  ...  TAX_CLASS_AT_PRESENT_1D
0                       1  ...                        0
1                       0  ...                        0
2                       0  ...                        0
3                       1  ...                        0
4                       0  ...                        0

[5 rows x 10 columns]

# Feature Selection with *SelectKBest*

In [17]:
train_subset = train.select_dtypes('number').dropna(axis='columns')
test_subset  = test.select_dtypes('number').dropna(axis='columns')
assert all(train_subset.columns == test_subset.columns)

target = 'SALE_PRICE'
features = train_subset.columns.drop(target)
X_train = train_subset[features]
y_train = train_subset[target]
X_test  = test_subset[features]
y_test  = test_subset[target]
X_train.shape, y_train.shape, X_test.shape, y_test.shape

KeyError: ignored

In [14]:
from sklearn.feature_selection import f_regression, SelectKBest

selector = SelectKBest(score_func=f_regression, k=10)
X_train_selected = selector.fit_transform(X_train, y_train)
X_test_selected = selector.transform(X_test)

X_train_selected.shape, X_test_selected.shape

NameError: ignored

In [0]:
all_names = X_train.columns
selected_mask = selector.get_support()
selected_names = all_names[selected_mask]
unselected_names = all_names[~selected_mask]

print('Features selected:')
for name in selected_names:
    print(name)

print('\nFeatures not selected:')
for name in unselected_names:
    print(name)

# Linear Regression Model with Multiple Features

# Absolute Mean Error for test set

# Organizing and commenting Code

In [0]:
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_absolute_error
from sklearn.feature_selection import f_regression, SelectKBest


target = 'SALE_PRICE'
high_cardinality = ['ADDRESS', 'LAND_SQUARE_FEET', 'APARTMENT_NUMBER', 'NEIGHBORHOOD',
                    'BUILDING_CLASS_AT_TIME_OF_SALE', 'BUILDING_CLASS_AT_PRESENT',
                    'SALE_DATE', 'BUILDING_CLASS_CATEGORY']
features = train.columns.drop([target] + high_cardinality)

X_train = train[features]
y_train = train[target]

X_test = test[features]
y_test = test[target]

encoder = ce.OneHotEncoder(use_cat_names=True)
X_train_encoded = encoder.fit_transform(X_train)
X_test_encoded = encoder.transform(X_test)

scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train_encoded)
X_test_scaled = scaler.transform(X_test_encoded)

for k in range(1, len(X_train.columns)+1):
  print(f'{k} features')
  
  selector = SelectKBest(score_func=f_regression, k=k)
  X_train_selected = selector.fit_transform(X_train_scaled, y_train)
  X_test_selected = selector.transform(X_test_scaled)
  
  model = LinearRegression()
  model.fit(X_train_selected, y_train)
  
  y_pred = model.predict(X_train_selected, y_train)
  mae = mean_absolute_error(y_test, y_pred)
  print(f'Test MAE: ${mae:,.0f} \n')